# Import Libraries

In [1]:
!pip install gensim
!pip install kaggle
!pip install textblob
!pip install pyspellchecker
!pip install fuzzywuzzy
!pip install python-Levenshtein
import pandas as pd
import numpy as np
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
import re
from gensim.models import Word2Vec
from spellchecker import SpellChecker
from textblob import TextBlob
from fuzzywuzzy import fuzz
from fuzzywuzzy import process
import glob
import spacy
nlp = spacy.load('en_core_web_sm')
from nltk.corpus import stopwords
import string
from collections import Counter
from collections import OrderedDict
from nltk.tokenize import sent_tokenize
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from nltk.stem.porter import PorterStemmer
from nltk.corpus import stopwords
from nltk.stem.snowball import SnowballStemmer
from nltk.stem.porter import *
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('omw-1.4')
nltk.download('stopwords')


[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\malak\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\malak\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\malak\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\malak\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

# Importing dataset


In [2]:
!mkdir ~/.kaggle
!move kaggle.json C:\Users\malak\.kaggle.

The syntax of the command is incorrect.
The system cannot find the file specified.


In [3]:
!kaggle datasets download -d notshrirang/spotify-million-song-dataset

spotify-million-song-dataset.zip: Skipping, found more recently modified local copy (use --force to force download)


In [4]:
!unzip spotify-million-song-dataset.zip

'unzip' is not recognized as an internal or external command,
operable program or batch file.


In [5]:
spotifyDF = pd.read_csv("spotify_millsongdata.csv")

# Data Exploration

In [6]:
spotifyDF.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 57650 entries, 0 to 57649
Data columns (total 4 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   artist  57650 non-null  object
 1   song    57650 non-null  object
 2   link    57650 non-null  object
 3   text    57650 non-null  object
dtypes: object(4)
memory usage: 1.8+ MB


In [7]:
spotifyDF.columns

Index(['artist', 'song', 'link', 'text'], dtype='object')

In [8]:
spotifyDF.head(10)

artist                   song                                        link  \
0   ABBA  Ahe's My Kind Of Girl  /a/abba/ahes+my+kind+of+girl_20598417.html   
1   ABBA       Andante, Andante       /a/abba/andante+andante_20002708.html   
2   ABBA         As Good As New        /a/abba/as+good+as+new_20003033.html   
3   ABBA                   Bang                  /a/abba/bang_20598415.html   
4   ABBA       Bang-A-Boomerang      /a/abba/bang+a+boomerang_20002668.html   
5   ABBA     Burning My Bridges    /a/abba/burning+my+bridges_20003011.html   
6   ABBA              Cassandra             /a/abba/cassandra_20002811.html   
7   ABBA             Chiquitita            /a/abba/chiquitita_20002978.html   
8   ABBA            Crazy World           /a/abba/crazy+world_20003013.html   
9   ABBA        Crying Over You       /a/abba/crying+over+you_20177611.html   

                                                text  
0  Look at her face, it's a wonderful face  \r\nA...  
1  Take it easy with me, please  \r\nTouch me gen...  
2  I'll never know why I had to go  \r\nWhy I had...  
3  Making somebody happy is a question of give an...  
4  Making somebody happy is a question of give an...  
5  Well, you hoot and you holler and you make me ...  
6  Down in the street they're all singing and sho...  
7  Chiquitita, tell me what's wrong  \r\nYou're e...  
8  I was out with the morning sun  \r\nCouldn't s...  
9  I'm waitin' for you baby  \r\nI'm sitting all ...

In [9]:
spotifyDF.nunique()

artist      643
song      44824
link      57650
text      57494
dtype: int64

In [10]:
spotifyDF.song.value_counts()

song
Have Yourself A Merry Little Christmas    35
Angel                                     28
Hold On                                   27
Home                                      27
I Believe                                 26
                                          ..
Just Be Good (Bushman Dub)                 1
Kingston Town                              1
Kiss And Say Goodbye                       1
Lambsbread                                 1
Generation                                 1
Name: count, Length: 44824, dtype: int64

In [11]:
spotifyDF.text.value_counts()

text
I just came back from a lovely trip along the Milky Way  \r\nStopped off at the North Pole to spend a holiday  \r\nI called on dear old Santa Claus  \r\nTo see what I could see  \r\nHe took me to his workshop  \r\nAnd told his plans to me, so  \r\n  \r\n[Chorus]  \r\nYou better watch out, you better not cry  \r\nBetter not pout, I'm telling you why  \r\nSanta Claus is comin' to town  \r\nHe's making a list and checking it twice  \r\nGonna find out who's naughty and nice  \r\nSanta Claus is comin' to town  \r\nHe sees you when you're sleepin'  \r\nHe knows when you're a wake  \r\nHe knows if you've been bad or good  \r\nSo be good for goodness sake  \r\nOh! You better watch out, you better not cry  \r\nBetter not pout, I'm telling you why  \r\nSanta Claus is comin' to town  \r\n  \r\nWith little tin horns and little toy drums  \r\nRooty toot toots and rummy tum tums  \r\nSanta Claus is comin' to town  \r\nAnd curly head dolls that toddle and coo  \r\nElephants, boats, and kiddie ca

# Data Cleaning

## Remove null values

In [12]:
spotifyDFCopy=spotifyDF.copy()

In [13]:
spotifyDFCopy.isnull().mean()*100

artist    0.0
song      0.0
link      0.0
text      0.0
dtype: float64

No null values are present in the dataset

##  Remove Full row duplicates

In [14]:
spotifyDFCopy.duplicated().sum()

0

No full row duplicates are present in the dataset

## Tokenization and Lemmatization

In [15]:
def dataframe_to_texts(df):
    texts = df['text'].tolist()
    return texts

In [16]:
texts=dataframe_to_texts(spotifyDFCopy)
texts

["Look at her face, it's a wonderful face  \r\nAnd it means something special to me  \r\nLook at the way that she smiles when she sees me  \r\nHow lucky can one fellow be?  \r\n  \r\nShe's just my kind of girl, she makes me feel fine  \r\nWho could ever believe that she could be mine?  \r\nShe's just my kind of girl, without her I'm blue  \r\nAnd if she ever leaves me what could I do, what could I do?  \r\n  \r\nAnd when we go for a walk in the park  \r\nAnd she holds me and squeezes my hand  \r\nWe'll go on walking for hours and talking  \r\nAbout all the things that we plan  \r\n  \r\nShe's just my kind of girl, she makes me feel fine  \r\nWho could ever believe that she could be mine?  \r\nShe's just my kind of girl, without her I'm blue  \r\nAnd if she ever leaves me what could I do, what could I do?\r\n\r\n",
 "Take it easy with me, please  \r\nTouch me gently like a summer evening breeze  \r\nTake your time, make it slow  \r\nAndante, Andante  \r\nJust let the feeling grow  \r\n 

In [17]:
def tokenize_column(array):
    lemma_list_Final = []
    for text in array:
        doc = nlp(text)
        lemma_list=[]
        for token in doc:
            lemma_list.append(token.lemma_)
        lemma_list_Final.append(lemma_list)
    return lemma_list_Final

In [18]:
token_list=[]
token_list=tokenize_column(texts)
token_list

## Stop words removal

In [ ]:
def remove_stop_words(token_list):
    no_stop_words_final = []
    for word_array in token_list:
        no_stop_words = []
        for word in word_array:
            if not nlp.vocab[word].is_stop:
                no_stop_words.append(word)
        no_stop_words_final.append(no_stop_words)
    return no_stop_words_final

In [ ]:
no_stop_words=[]
no_stop_words=remove_stop_words(token_list)
no_stop_words

[['look',
  'face',
  ',',
  'wonderful',
  'face',
  ' \r\n',
  'mean',
  'special',
  ' \r\n',
  'look',
  'way',
  'smile',
  ' \r\n',
  'lucky',
  'fellow',
  '?',
  ' \r\n  \r\n',
  'kind',
  'girl',
  ',',
  'feel',
  'fine',
  ' \r\n',
  'believe',
  '?',
  ' \r\n',
  'kind',
  'girl',
  ',',
  'blue',
  ' \r\n',
  'leave',
  ',',
  '?',
  ' \r\n  \r\n',
  'walk',
  'park',
  ' \r\n',
  'hold',
  'squeeze',
  'hand',
  ' \r\n',
  'walk',
  'hour',
  'talk',
  ' \r\n',
  'thing',
  'plan',
  ' \r\n  \r\n',
  'kind',
  'girl',
  ',',
  'feel',
  'fine',
  ' \r\n',
  'believe',
  '?',
  ' \r\n',
  'kind',
  'girl',
  ',',
  'blue',
  ' \r\n',
  'leave',
  ',',
  '?',
  '\r\n\r\n'],
 ['easy',
  ',',
  ' \r\n',
  'touch',
  'gently',
  'like',
  'summer',
  'evening',
  'breeze',
  ' \r\n',
  'time',
  ',',
  'slow',
  ' \r\n',
  'Andante',
  ',',
  'Andante',
  ' \r\n',
  'let',
  'feeling',
  'grow',
  ' \r\n  \r\n',
  'finger',
  'soft',
  'light',
  ' \r\n',
  'let',
  'body',
  

## Remove Punctuation

In [ ]:
punctuations="?:!.,;"
def remove_punctuation(no_stop_words):
    for array_with_stop_words in no_stop_words:
        for word in array_with_stop_words:
            if word in punctuations:
                array_with_stop_words.remove(word)
    return no_stop_words

In [ ]:
no_punctuations=[]
no_punctuations=remove_punctuation(no_stop_words)
no_punctuations

[['look',
  'face',
  'wonderful',
  'face',
  ' \r\n',
  'mean',
  'special',
  ' \r\n',
  'look',
  'way',
  'smile',
  ' \r\n',
  'lucky',
  'fellow',
  ' \r\n  \r\n',
  'kind',
  'girl',
  'feel',
  'fine',
  ' \r\n',
  'believe',
  ' \r\n',
  'kind',
  'girl',
  'blue',
  ' \r\n',
  'leave',
  ' \r\n  \r\n',
  'walk',
  'park',
  ' \r\n',
  'hold',
  'squeeze',
  'hand',
  ' \r\n',
  'walk',
  'hour',
  'talk',
  ' \r\n',
  'thing',
  'plan',
  ' \r\n  \r\n',
  'kind',
  'girl',
  'feel',
  'fine',
  ' \r\n',
  'believe',
  '?',
  ' \r\n',
  'kind',
  'girl',
  'blue',
  ' \r\n',
  'leave',
  '?',
  '\r\n\r\n'],
 ['easy',
  ' \r\n',
  'touch',
  'gently',
  'like',
  'summer',
  'evening',
  'breeze',
  ' \r\n',
  'time',
  'slow',
  ' \r\n',
  'Andante',
  'Andante',
  ' \r\n',
  'let',
  'feeling',
  'grow',
  ' \r\n  \r\n',
  'finger',
  'soft',
  'light',
  ' \r\n',
  'let',
  'body',
  'velvet',
  'night',
  ' \r\n',
  'touch',
  'soul',
  'know',
  ' \r\n',
  'Andante',
  'A

## Spell checker

In [ ]:
spell = SpellChecker()
def correct_spell(no_punctuations):
    corrected_textfinal = []
    for array in no_punctuations:
        corrected_text=[]
        for word in array:
            if(spell.correction(word)is not None):
                corrected_text.append(spell.correction(word))
        corrected_textfinal.append(corrected_text)
    return corrected_textfinal

In [ ]:
correct_spelling=[]
correct_spelling=correct_spell(no_punctuations)
correct_spelling

[['look',
  'face',
  'wonderful',
  'face',
  'mean',
  'special',
  'look',
  'way',
  'smile',
  'lucky',
  'fellow',
  'kind',
  'girl',
  'feel',
  'fine',
  'believe',
  'kind',
  'girl',
  'blue',
  'leave',
  'walk',
  'park',
  'hold',
  'squeeze',
  'hand',
  'walk',
  'hour',
  'talk',
  'thing',
  'plan',
  'kind',
  'girl',
  'feel',
  'fine',
  'believe',
  '?',
  'kind',
  'girl',
  'blue',
  'leave',
  '?']]

In [ ]:
spotifyDFCopy['text_cleaned'] = correct_spelling

# Data Analysis

## Term, Document Frequencies

In [ ]:
def generate_vocab(array_of_arrays):
    tokens_set = set(token for word_array in array_of_arrays for token in word_array)
    vocab = list(tokens_set)
    return vocab

In [ ]:
vocab = generate_vocab(correct_spelling)
print(vocab)

In [ ]:
def termFrequencyInDoc(arrayOfArrays,vocab):
    tf_docs = {}
    for index, array in enumerate(arrayOfArrays):
        tf_docs[index] = {}    

        for word in vocab:
            tf_docs[index][word] = array.count(word)
    return tf_docs

In [ ]:
# test=[["Andrew","Malak"],["Malak","Ziad"]]
tf_docs=termFrequencyInDoc(correct_spelling,vocab)
tf_docs

In [ ]:
from collections import Counter

def wordDocFre(array_of_arrays):
    all_tokens = [token for word_array in array_of_arrays for token in word_array]
    tf_across_docs = dict(Counter(all_tokens))
    return tf_across_docs

In [ ]:
tf_across_docs = wordDocFre(correct_spelling)
print(tf_across_docs)

In [ ]:
def inverseDocFre(vocab,doc_fre,length):
    idf= {} 
    for word in vocab:     
        idf[word] = np.log2((length+1) / doc_fre[word])
    return idf

In [ ]:
length=spotifyDFCopy['text'].count()
idF=inverseDocFre(vocab,tf_across_docs,length)
idF

In [ ]:
from collections import defaultdict

def tfidf(vocab, tf, idf_scr, array_of_arrays):
    tf_idf_scr = defaultdict(dict)
    for word in vocab:
        for doc_id, word_array in enumerate(array_of_arrays):
            tf_idf_scr[doc_id][word] = tf[doc_id].get(word, 0) * idf_scr.get(word, 0)
    
    for doc_id, scores in tf_idf_scr.items():
        tf_idf_scr[doc_id] = {word: tf_idf for word, tf_idf in sorted(scores.items(), key=lambda x: x[1], reverse=True)}
    
    return dict(tf_idf_scr)

In [ ]:
tf_idf_scr = tfidf(vocab, tf_docs, idF, correct_spelling)
print(tf_idf_scr)

## Most Frequent Class

spotifyDFCopy['artist'].value_counts().head(10)

## Frequency of songs per artist

## Words in lyrics per song

## Repetition of words in a song